In [1]:
import pandas as pd
import numpy as np
import re
from tqdm.auto import tqdm

In [6]:
# load data
df = pd.read_excel("/content/titktok_comments.xlsx")
df

username                                  text
0    bts_official_bighit                    I MISSED YOU GUYSS
1    bts_official_bighit       we love you so much namjoon🥰💜💜💜
2        roses_are_rosie              haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋
3              bp_tiktok  BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥
4          jypestraykids  me encanta el humor de Changbin 😭😭❤️
..                   ...                                   ...
179    hannahmchutchison                                 ne ne
180             raianu07                                   🥰🥰🥰
181             hsnnbinn     라이브 못본거 진짜 관짝 들어갈때까지의 한이 될거같습니다…🥺
182         wearedrippin                             MY BABIES
183             hhhsh999                            발스텝부터 알아봣따

[184 rows x 2 columns]

# **Translate**

In [8]:
!pip install --quiet deep-translator
from deep_translator import GoogleTranslator
gt = GoogleTranslator(source='auto', target='en')

In [9]:
# translate
for i in tqdm(range(len(df))):
  text = df.loc[i,'text']
  df.loc[i,'translated'] = gt.translate(text)

df.dropna(inplace=True) # this simplifies things later on!!!
df.reset_index(drop=True, inplace=True)
df

  0%|          | 0/184 [00:00<?, ?it/s]

username                                  text  \
0    bts_official_bighit                    I MISSED YOU GUYSS   
1    bts_official_bighit       we love you so much namjoon🥰💜💜💜   
2        roses_are_rosie              haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋   
3              bp_tiktok  BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥   
4          jypestraykids  me encanta el humor de Changbin 😭😭❤️   
..                   ...                                   ...   
153    wildwild_official                             足なっっっっっげえ   
154    hannahmchutchison                                 ne ne   
155             hsnnbinn     라이브 못본거 진짜 관짝 들어갈때까지의 한이 될거같습니다…🥺   
156         wearedrippin                             MY BABIES   
157             hhhsh999                            발스텝부터 알아봣따   

                                            translated  
0                                   I MISSED YOU GUYSS  
1                      we love you so much namjoon🥰💜💜💜  
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋  
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥  
4                         I love Changbin's humor 😭😭❤️  
..                                                 ...  
153                                 My legs are so big  
154                                              ne ne  
155  I think not being able to see it live will be ...  
156                                          MY BABIES  
157                  I learned it from the foot steps.  

[158 rows x 3 columns]

# Let's prepare a function to clean text, based on **SpaCy**

In [10]:
import spacy
!pip install --quiet spacymoji
from spacymoji import Emoji
nlp = spacy.load('en_core_web_sm')
nlp.tokenizer.token_match = re.compile("^#\w+$").match
nlp.add_pipe("emoji", first=True)

import emoji
def get_emoji_regexp():
    # Sort emoji by length to make sure multi-character emojis are
    # matched first
    emojis = sorted(emoji.EMOJI_DATA, key=len, reverse=True)
    pattern = '(' + '|'.join(re.escape(u) for u in emojis) + ')'
    return re.compile(pattern)

<>:5: SyntaxWarning: invalid escape sequence '\w'
<>:5: SyntaxWarning: invalid escape sequence '\w'
/tmp/ipython-input-4268926626.py:5: SyntaxWarning: invalid escape sequence '\w'
  nlp.tokenizer.token_match = re.compile("^#\w+$").match


In [11]:
# a function to clean text that uses what we have seen in the spacy lab
#
# with text_form you can choose the external format (list or text)
#
# with to_keep you can choose if you want to keep or remove certain PoS
#
# with kr_list you can choose which POS tags to keep or remove,
# to be chosen from the following list
#
# Universal POS Tags http://universaldependencies.org/u/pos/
#
#   "ADJ": "adjective",
#   "ADP": "adposition",
#   "ADV": "adverb",
#   "AUX": "auxiliary",
#   "CONJ": "conjunction",
#   "CCONJ": "coordinating conjunction",
#   "DET": "determiner",
#   "INTJ": "interjection",
#   "NOUN": "noun",
#   "NUM": "numeral",
#   "PART": "particle",
#   "PRON": "pronoun",
#   "PROPN": "proper noun",
#   "PUNCT": "punctuation",
#   "SCONJ": "subordinating conjunction",
#   "SYM": "symbol",
#   "VERB": "verb",
#   "X": "other",
#   "EOL": "end of line",
#   "SPACE": "space"
#
# Internal tags
#
#   "EMOJI" emojis,
#   "HASH" hastags
#   "HTML" web links,
#   "MENT" mentions
#
def clean_text(text, text_form=True, to_keep=True,
               kr_list = ["ADJ","ADV","EMOJI","HASH","NOUN","PROPN","VERB"]):

    # apply spacy
    doc = nlp(" ".join(get_emoji_regexp().split(text)))
    # collect spacy outomes in in a list
    out = list()
    for token in doc:
        out.append((token.text, token.text+token.whitespace_,
                    token.lemma_.lower(), token.pos_,
                    token.text.startswith("#"),
                    token.text.startswith("@"),
                    emoji.purely_emoji(token.text),
                    (token.text.startswith("https:") or token.text.startswith("http:"))
                    ))
    # turn it into a dataframe
    df2 = pd.DataFrame(out)
    df2.columns = ['text', 'full_text', 'lemma', 'PoS',
                   'is_hashtag', 'is_mention', 'is_emoji', 'is_link']
    # build a PoS column that identifies hashtags, mentions, etc
    df2.insert(loc = 4, column = 'myPoS', value = df2['PoS'])
    df2.loc[df2['is_hashtag']==True,'myPoS'] = 'HASH'
    df2.loc[df2['is_mention']==True,'myPoS'] = 'MENT'
    df2.loc[df2['is_emoji']==True,'myPoS'] = 'EMOJI'
    df2.loc[df2['is_link']==True,'myPoS'] = 'HTML'
    # replace emojis lemmas with their description
    for tmp in doc._.emoji:
      df2.loc[tmp[1],'lemma'] = tmp[0]+" "+tmp[2]
    # keep/remove only what is asked
    if text_form:
      if to_keep:
        out = [j for (i,j) in zip(df2['myPoS'],df2['full_text']) if i in kr_list]
      else:
        out = [j for (i,j) in zip(df2['myPoS'],df2['full_text']) if i not in kr_list]
      return "".join(out)
    else:
      if to_keep:
        out = [j for (i,j) in zip(df2['myPoS'],df2['lemma']) if i in kr_list]
      else:
        out = [j for (i,j) in zip(df2['myPoS'],df2['lemma']) if i not in kr_list]
      return out

# **Clean** text

In [47]:
df2 = df[['translated']].copy()

# clean text
for i in tqdm(range(len(df2))):
  text = df2.loc[i,'translated']
  df2.loc[i,'clean text'] = clean_text(text, text_form=True,
                                         to_keep=True,
                                         kr_list=["PRON","ADJ","ADV","HASH","NOUN","PROPN","VERB"])
  df2.loc[[i],'clean list'] = pd.Series([
                             clean_text(text, text_form=False,
                                              to_keep=True,
                                              kr_list=["PRON","ADJ","ADV","HASH","NOUN","PROPN","VERB"])
                             ], index=[i])
df2

  0%|          | 0/158 [00:00<?, ?it/s]

translated  \
0                                   I MISSED YOU GUYSS   
1                      we love you so much namjoon🥰💜💜💜   
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋   
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥   
4                         I love Changbin's humor 😭😭❤️   
..                                                 ...   
153                                 My legs are so big   
154                                              ne ne   
155  I think not being able to see it live will be ...   
156                                          MY BABIES   
157                  I learned it from the foot steps.   

                                            clean text  \
0                                   I MISSED YOU GUYSS   
1                         we love you so much namjoon    
2                                             hatersBP   
3                          BLACKPINK BEST GROUP WORLD    
4                                I love Changbinhumor    
..                                                 ...   
153                                     My legs so big   
154                                              ne ne   
155  I think able see it live regret I get back coffin   
156                                          MY BABIES   
157                            I learned it foot steps   

                                            clean list  
0                                 [i, miss, you, guys]  
1                   [we, love, you, so, much, namjoon]  
2                                          [hater, bp]  
3                      [blackpink, best, group, world]  
4                           [i, love, changbin, humor]  
..                                                 ...  
153                                 [my, leg, so, big]  
154                                           [ne, ne]  
155  [i, think, able, see, it, live, regret, i, get...  
156                                         [my, baby]  
157                         [i, learn, it, foot, step]  

[158 rows x 3 columns]

# Identify **emojis**

In [28]:
df2 = df[['text']].copy()

# detect emojis
for i in tqdm(range(len(df2))):
  text = df2.loc[i,'text']
  df2.loc[i,'emojis'] = clean_text(text, text_form=True,
                                         to_keep=True,
                                         kr_list=["EMOJI"])
  df2.loc[[i],'emojis list'] = pd.Series([
                             clean_text(text, text_form=False,
                                              to_keep=True,
                                              kr_list=["EMOJI"])
                             ], index=[i])
df2

  0%|          | 0/158 [00:00<?, ?it/s]

text                emojis  \
0                      I MISSED YOU GUYSS                         
1         we love you so much namjoon🥰💜💜💜              🥰 💜 💜 💜    
2                haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋  🙄 😡 😤 🦣 🎃 💗 🫦 🎀 💸 💋    
3    BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥                💯 🔥 🔥    
4    me encanta el humor de Changbin 😭😭❤️               😭 😭 ❤️    
..                                    ...                   ...   
153                             足なっっっっっげえ                         
154                                 ne ne                         
155     라이브 못본거 진짜 관짝 들어갈때까지의 한이 될거같습니다…🥺                    🥺    
156                             MY BABIES                         
157                            발스텝부터 알아봣따                         

                                           emojis list  
0                                                   []  
1    [🥰 smiling face with hearts, 💜 purple heart, 💜...  
2    [🙄 face with rolling eyes, 😡 enraged face, 😤 f...  
3                   [💯 hundred points, 🔥 fire, 🔥 fire]  
4    [😭 loudly crying face, 😭 loudly crying face, ❤...  
..                                                 ...  
153                                                 []  
154                                                 []  
155                                  [🥺 pleading face]  
156                                                 []  
157                                                 []  

[158 rows x 3 columns]

# Extract **emotions**

In [29]:
# https://huggingface.co/cardiffnlp/twitter-roberta-large-emotion-latest
#
from transformers import pipeline
pipe = pipeline('text-classification',
                model="cardiffnlp/twitter-roberta-large-emotion-latest",
                return_all_scores=True)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
Device set to use cpu
/usr/local/lib/python3.12/dist-packages/transformers/pipelines/text_classification.py:111: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


In [30]:
df2 = df[['translated']].copy()

# get emotions
for i in tqdm(range(len(df2))):
  text = df2.loc[i,'translated']
  predictions = pipe(text)[0]
  for j in range(len(predictions)):
    df2.loc[i, predictions[j]['label']] = round(predictions[j]['score'],4)

df2

  0%|          | 0/158 [00:00<?, ?it/s]

translated   anger  anticipation  \
0                                   I MISSED YOU GUYSS  0.0121        0.0890   
1                      we love you so much namjoon🥰💜💜💜  0.0183        0.0224   
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋  0.9528        0.0583   
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥  0.0203        0.2438   
4                         I love Changbin's humor 😭😭❤️  0.0136        0.0297   
..                                                 ...     ...           ...   
153                                 My legs are so big  0.0138        0.1850   
154                                              ne ne  0.0241        0.0774   
155  I think not being able to see it live will be ...  0.0114        0.1195   
156                                          MY BABIES  0.0137        0.0416   
157                  I learned it from the foot steps.  0.0061        0.4315   

     disgust    fear     joy    love  optimism  pessimism  sadness  surprise  \
0     0.0381  0.0474  0.1375  0.2628    0.0180     0.1967   0.9927    0.0232   
1     0.0183  0.0096  0.9826  0.9934    0.4805     0.0186   0.0637    0.0150   
2     0.4327  0.0054  0.8497  0.0789    0.5624     0.0130   0.0477    0.0095   
3     0.0112  0.0068  0.9874  0.8841    0.6740     0.0142   0.0147    0.1182   
4     0.0149  0.0113  0.9856  0.9942    0.5646     0.0188   0.0732    0.0193   
..       ...     ...     ...     ...       ...        ...      ...       ...   
153   0.0256  0.2976  0.5866  0.0316    0.1099     0.0345   0.2241    0.2603   
154   0.0888  0.0284  0.0159  0.0024    0.0128     0.0415   0.1520    0.0087   
155   0.0499  0.0344  0.0823  0.0305    0.0493     0.4038   0.9966    0.0183   
156   0.0367  0.0604  0.7553  0.9666    0.0974     0.0536   0.7570    0.0205   
157   0.0093  0.0165  0.0962  0.0099    0.5374     0.0292   0.0271    0.0167   

      trust  
0    0.0251  
1    0.0883  
2    0.0380  
3    0.6141  
4    0.1168  
..      ...  
153  0.0221  
154  0.0044  
155  0.0148  
156  0.0484  
157  0.1124  

[158 rows x 12 columns]

# Extract **sentiment**

In [31]:
# https://huggingface.co/cardiffnlp/twitter-roberta-base-sentiment-latest
#
from transformers import pipeline
model_path = f"cardiffnlp/twitter-roberta-base-sentiment-latest"
sentiment_task = pipeline("sentiment-analysis",
                          model=model_path,
                          tokenizer=model_path)

Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Device set to use cpu


In [32]:
df2 = df[['translated']].copy()

# get sentiment
for i in tqdm(range(len(df2))):
  text= df2.loc[i,'translated']
  predictions = sentiment_task(text)[0]
  df2.loc[i, 'sentiment'] = predictions['label']
  df2.loc[i, 'score'] = round(predictions['score'],4)

df2

  0%|          | 0/158 [00:00<?, ?it/s]

translated sentiment   score
0                                   I MISSED YOU GUYSS  positive  0.9299
1                      we love you so much namjoon🥰💜💜💜  positive  0.9859
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋  negative  0.4806
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥  positive  0.9798
4                         I love Changbin's humor 😭😭❤️  positive  0.9793
..                                                 ...       ...     ...
153                                 My legs are so big   neutral  0.4214
154                                              ne ne   neutral  0.5957
155  I think not being able to see it live will be ...  negative  0.8737
156                                          MY BABIES  positive  0.9029
157                  I learned it from the foot steps.   neutral  0.6420

[158 rows x 3 columns]

# Let's prepare a function that runs **BERTAgent**

In [33]:
!pip install ftfy --quiet
import ftfy

In [34]:
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from transformers import AutoTokenizer, RobertaTokenizer, RobertaModel, AutoModelForSequenceClassification
from transformers import get_linear_schedule_with_warmup

In [35]:
# check if we have cuda installed
if torch.cuda.is_available():
    # to use GPU
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('GPU is:', torch.cuda.get_device_name(0))
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

No GPU available, using the CPU instead.


In [36]:
# This mimics BERTAgent but it can work in the absence of GPU resources,
# although slow in that case

class agency():
    def __init__(self):
        # see https://bertagent.readthedocs.io/en/latest/
        model_name = "EnchantedStardust/bertagent-best"
        revision = "5bae55efbd95dd51759d275410cea36c81109227"

        # tokenizer
        self.tokenizer = AutoTokenizer.from_pretrained(model_name,
                                                       do_lower_case = True,
                                                       revision = revision)
        # roberta model
        self.model = AutoModelForSequenceClassification.from_pretrained(
                model_name,
                num_labels = 1,
                revision = revision
            ).to(device)

    def extract_agency(self, text, BATCH_SIZE=10):

        # clean sentences (the way BERTAgent does)
        text = self._clean_sentences(text)

        # tokenize documents
        tokenized_text = self.tokenizer(
            text,
            add_special_tokens = True,
            padding = "max_length",
            truncation = True,
            max_length = 128,
            return_attention_mask = True,
            return_tensors = 'pt',
            return_token_type_ids = False,
            return_offsets_mapping = False,
        )

        # create the dataloader
        data = TensorDataset(tokenized_text['input_ids'],
                             tokenized_text['attention_mask'])
        dataloader = DataLoader(data,
                                batch_size = BATCH_SIZE)

        self.model = self.model.eval()
        out = [] # tokens + attributions

        # loop on batches
        for batch in tqdm(dataloader, desc="Evaluating"):

            # load data from dataloader
            b_input_ids = batch[0].to(device)
            b_input_mask = batch[1].to(device)

            # extract embeddings
            b_embedd = self.model.roberta.embeddings.word_embeddings(
                                                   b_input_ids).detach()

            # evaluate agency
            agency = self.model.forward(inputs_embeds = b_embedd,
                                        attention_mask = b_input_mask)

            # add the result to the list
            out.append(agency['logits'].detach().cpu())

        # map the result into a dataframe
        out = np.concatenate(out)
        return out

    def _clean_sentences(self, sentences):
        sentences = [re.sub(r"\s\s+", " ", sent).strip() for sent in sentences]
        sentences = [ftfy.fix_text(sent) for sent in sentences] # fix text
        return sentences

# Extract agency by **BERTAgent**

In [37]:
# instantiate an element for BERTAgent
ba0 = agency()

# Evaluate agency on the translated text (it works on English only)
# ... can be very slow if run on CPU!!!
# ... better do in chunks for large number of texts!!!
df2 = df[['translated']].copy()
df2['agency'] = ba0.extract_agency(list(df2['translated']), BATCH_SIZE=20)
df2

Evaluating:   0%|          | 0/8 [00:00<?, ?it/s]

translated    agency
0                                   I MISSED YOU GUYSS -0.331446
1                      we love you so much namjoon🥰💜💜💜  0.009748
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋 -0.261824
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥  0.058124
4                         I love Changbin's humor 😭😭❤️  0.077732
..                                                 ...       ...
153                                 My legs are so big -0.065885
154                                              ne ne -0.124783
155  I think not being able to see it live will be ... -0.230997
156                                          MY BABIES  0.024777
157                  I learned it from the foot steps.  0.133080

[158 rows x 2 columns]

# Extract **LIWC features** by Python
*(similar to what the true LIWC does!)*

In [38]:
!pip install --quiet contentcoder
from contentcoder.ContentCoder import ContentCoder
# instantiate coder class
cc = ContentCoder(dicFilename='/content/LIWC2007_English100131.dic',
                  fileEncoding='utf-8-sig')

Dictionary loaded.


In [39]:
df2 = df[['translated']].copy()

# get many different features by LIWC dictionary
for i in tqdm(range(len(df2))):
  text = df2.loc[i,'translated']
  results = cc.Analyze(text, relativeFreq=True,
                             dropPunct=True,
                             retainCaptures=False,
                             returnTokens=False,
                             wildcardMem=True)
  for m in results.keys():
    df2.loc[i,m] = results[m]

df2

  0%|          | 0/158 [00:00<?, ?it/s]

translated         Dic    WC  \
0                                   I MISSED YOU GUYSS  100.000000   4.0   
1                      we love you so much namjoon🥰💜💜💜   50.000000  10.0   
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋    8.333333  12.0   
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥   55.555556   9.0   
4                         I love Changbin's humor 😭😭❤️   37.500000   8.0   
..                                                 ...         ...   ...   
153                                 My legs are so big  100.000000   5.0   
154                                              ne ne    0.000000   2.0   
155  I think not being able to see it live will be ...   90.476190  21.0   
156                                          MY BABIES  100.000000   2.0   
157                  I learned it from the foot steps.  100.000000   7.0   

      BigWords  Numbers  AllPunct    Period  Comma  QMark  Exclam  ...  \
0     0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
1    10.000000      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
2     0.000000      0.0  0.166667  0.000000    0.0    0.0     0.0  ...   
3    11.111111      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
4    12.500000      0.0  0.125000  0.000000    0.0    0.0     0.0  ...   
..         ...      ...       ...       ...    ...    ...     ...  ...   
153   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
154   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
155   0.000000      0.0  0.142857  0.142857    0.0    0.0     0.0  ...   
156   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0  ...   
157  14.285714      0.0  0.142857  0.142857    0.0    0.0     0.0  ...   

          work    achieve  leisure  home  money  relig     death  assent  \
0     0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
1     0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
2     0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
3     0.000000  11.111111      0.0   0.0    0.0    0.0  0.000000     0.0   
4     0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
..         ...        ...      ...   ...    ...    ...       ...     ...   
153   0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
154   0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
155   0.000000   4.761905      0.0   0.0    0.0    0.0  4.761905     0.0   
156   0.000000   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   
157  14.285714   0.000000      0.0   0.0    0.0    0.0  0.000000     0.0   

     nonfl  filler  
0      0.0     0.0  
1      0.0     0.0  
2      0.0     0.0  
3      0.0     0.0  
4      0.0     0.0  
..     ...     ...  
153    0.0     0.0  
154    0.0     0.0  
155    0.0     0.0  
156    0.0     0.0  
157    0.0     0.0  

[158 rows x 75 columns]

In [40]:
# this is what is available
[i for i in df2.columns]

['translated',
 'Dic',
 'WC',
 'BigWords',
 'Numbers',
 'AllPunct',
 'Period',
 'Comma',
 'QMark',
 'Exclam',
 'Apostro',
 'funct',
 'pronoun',
 'ppron',
 'i',
 'we',
 'you',
 'shehe',
 'they',
 'ipron',
 'article',
 'verb',
 'auxverb',
 'past',
 'present',
 'future',
 'adverb',
 'preps',
 'conj',
 'negate',
 'quant',
 'number',
 'swear',
 'social',
 'family',
 'friend',
 'humans',
 'affect',
 'posemo',
 'negemo',
 'anx',
 'anger',
 'sad',
 'cogmech',
 'insight',
 'cause',
 'discrep',
 'tentat',
 'certain',
 'inhib',
 'incl',
 'excl',
 'percept',
 'see',
 'hear',
 'feel',
 'bio',
 'body',
 'health',
 'sexual',
 'ingest',
 'relativ',
 'motion',
 'space',
 'time',
 'work',
 'achieve',
 'leisure',
 'home',
 'money',
 'relig',
 'death',
 'assent',
 'nonfl',
 'filler']

In [41]:
# can select a few
df2[['translated','i','we','body','social','past','future']]

translated          i    we  \
0                                   I MISSED YOU GUYSS  25.000000   0.0   
1                      we love you so much namjoon🥰💜💜💜   0.000000  10.0   
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋   0.000000   0.0   
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥   0.000000   0.0   
4                         I love Changbin's humor 😭😭❤️  12.500000   0.0   
..                                                 ...        ...   ...   
153                                 My legs are so big  20.000000   0.0   
154                                              ne ne   0.000000   0.0   
155  I think not being able to see it live will be ...   9.523810   0.0   
156                                          MY BABIES  50.000000   0.0   
157                  I learned it from the foot steps.  14.285714   0.0   

          body     social  past    future  
0     0.000000  50.000000  25.0  0.000000  
1     0.000000  30.000000   0.0  0.000000  
2     0.000000   0.000000   0.0  0.000000  
3     0.000000  11.111111   0.0  0.000000  
4     0.000000  12.500000   0.0  0.000000  
..         ...        ...   ...       ...  
153  20.000000   0.000000   0.0  0.000000  
154   0.000000   0.000000   0.0  0.000000  
155   0.000000   0.000000   0.0  4.761905  
156   0.000000  50.000000   0.0  0.000000  
157  14.285714   0.000000   0.0  0.000000  

[158 rows x 7 columns]

# Can also use **other** dictionaries

In [42]:
cc2 = ContentCoder(dicFilename='/content/big-two-agency-communion-dictionary.dicx',
                  fileEncoding='utf-8-sig')

Dictionary loaded.


In [43]:
df2 = df[['translated']].copy()

# get many different features by LIWC dictionary
for i in tqdm(range(len(df2))):
  text = df2.loc[i,'translated']
  results = cc2.Analyze(text, relativeFreq=True,
                             dropPunct=True,
                             retainCaptures=False,
                             returnTokens=False,
                             wildcardMem=True)
  for m in results.keys():
    df2.loc[i,m] = results[m]

df2

  0%|          | 0/158 [00:00<?, ?it/s]

translated        Dic    WC  \
0                                   I MISSED YOU GUYSS  25.000000   4.0   
1                      we love you so much namjoon🥰💜💜💜  30.000000  10.0   
2                             haters: 🙄😡😤🦣🎃\nBP: 💗🫦🎀💸💋   0.000000  12.0   
3                 BLACKPINK BEST GROUP IN THE WORLD💯🔥🔥  11.111111   9.0   
4                         I love Changbin's humor 😭😭❤️  12.500000   8.0   
..                                                 ...        ...   ...   
153                                 My legs are so big   0.000000   5.0   
154                                              ne ne   0.000000   2.0   
155  I think not being able to see it live will be ...  14.285714  21.0   
156                                          MY BABIES   0.000000   2.0   
157                  I learned it from the foot steps.  14.285714   7.0   

      BigWords  Numbers  AllPunct    Period  Comma  QMark  Exclam  Apostro  \
0     0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
1    10.000000      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
2     0.000000      0.0  0.166667  0.000000    0.0    0.0     0.0    0.000   
3    11.111111      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
4    12.500000      0.0  0.125000  0.000000    0.0    0.0     0.0    0.125   
..         ...      ...       ...       ...    ...    ...     ...      ...   
153   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
154   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
155   0.000000      0.0  0.142857  0.142857    0.0    0.0     0.0    0.000   
156   0.000000      0.0  0.000000  0.000000    0.0    0.0     0.0    0.000   
157  14.285714      0.0  0.142857  0.142857    0.0    0.0     0.0    0.000   

        Agency  Communion  
0    25.000000   0.000000  
1    10.000000  20.000000  
2     0.000000   0.000000  
3     0.000000  11.111111  
4     0.000000  12.500000  
..         ...        ...  
153   0.000000   0.000000  
154   0.000000   0.000000  
155  14.285714   0.000000  
156   0.000000   0.000000  
157   0.000000  14.285714  

[158 rows x 13 columns]